In [1]:
import utils.yolo_fun as yolo_fun
import utils.img_fun as img_fun
import os
import pandas as pd
from tqdm import tqdm  
import rasterio
from rasterio.windows import Window
from rasterio.errors import RasterioIOError
import numpy as np
import shutil

#valid_tiles = [13, 14, 15, 22, 23, 24, 35, 44, 45, 51, 52, 53, 54, 61, 62, 63, 70, 71, 72, 73, 81, 82]  

orthomosiac_coords = os.path.join('coords', 'yolo_coords.csv')
coords_dir_sin_normalizar = os.path.join('coords', 'labels_sin_normalizar')
coords_dir_normalized = os.path.join('coords', 'labels_normalized')
os.makedirs(coords_dir_sin_normalizar, exist_ok=True)
os.makedirs(coords_dir_normalized, exist_ok=True)

subrecortes_dir = os.path.join('cut_tiles')
os.makedirs(subrecortes_dir, exist_ok=True)
#path_doctorado = 'G:\\.shortcut-targets-by-id\\1pYgV5EIk4-LapLNhlCwpQaDAzuqNffXG\\doctorado_albert\\pinguiton\\ortho_dic_5000'
path_doctorado = 'G:\\.shortcut-targets-by-id\\1pYgV5EIk4-LapLNhlCwpQaDAzuqNffXG\\doctorado_albert\\conteo_pinguinos\\recortes'



In [2]:

# PARTE 0: ITERAMOS SOBRE LAS IMÁGENES PARA RECORTARLAS

contador = 0
for img in os.listdir(path_doctorado):
    
    try:
        # PARTE 1: Cargar la imagen y recortarla en imágenes más pequeñas de aproximadamente 500x500 píxeles
        print(f"\n\nRecortando imagen {img}...")
        print('_________________________________________________________')

        img_name = img.split('.')[0]
        

        tiff_file = os.path.join(path_doctorado, img_name + '.tif')


        # Sacamos un diccionario con toda la información de la imagen
        img_info = img_fun.get_img_info(tiff_file)
        WIDTH = img_info["width"]
        HEIGHT = img_info["height"]
        TOP_LEFT = img_info["top_left"]
        BOTTOM_RIGHT = img_info["bottom_right"]
        min_x, max_y = img_info['top_left']
        max_x, min_y = img_info['bottom_right']

        img_fun.crop_tile_into_subrecortes(
            tiff_file = tiff_file, 
            output_dir = subrecortes_dir, 
            coords_csv = orthomosiac_coords,
            tile_size = 640,
            overlap = 256
        )


        # PARTE 2 (OPCIONAL): EXTRACCIÓN DE METADATOS PARA CADA SUBRECORTE INDIVIUAL
        df_orthomosaic = pd.read_csv(orthomosiac_coords, encoding='ISO-8859-1')
        print("Datos Originales: \n", df_orthomosaic.head())

        # Filtrar los puntos que están dentro del tile
        filtered_data = df_orthomosaic[
            (df_orthomosaic['x_center'] >= min_x) & (df_orthomosaic['x_center'] <= max_x) &
            (df_orthomosaic['y_center'] >= min_y) & (df_orthomosaic['y_center'] <= max_y)
        ]
       # Asegúrate de que el directorio exista
        coords_per_tile = os.path.join('coords', 'coords_per_tile')
        os.makedirs(coords_per_tile, exist_ok=True)

        # Guarda el archivo CSV
        filtered_data.to_csv(os.path.join(coords_per_tile, f'coords_{img_name}.csv'), index=False)
        print(f"Datos filtrados guardados en 'coords/coords_per_tile/coords_{img_name}.csv'.")

     
    except RasterioIOError as e:
        print(f"Error al cargar la imagen con rasterio: {e}")
        continue
    except FileNotFoundError as e:
        print(f"Error: {e}")
        continue

    



Recortando imagen recorte_7.tif...
_________________________________________________________
Metadata:
---------
driver: GTiff
dtype: uint8
nodata: None
width: 10195
height: 11420
count: 4
crs: EPSG:4326
transform: | 0.00, 0.00,-59.21|
| 0.00,-0.00,-62.28|
| 0.00, 0.00, 1.00|
blockxsize: 10195
blockysize: 1
tiled: False
interleave: pixel

Coordenadas de las esquinas de la imagen:
TOP LEFT: (-59.21011298020679, -62.28453303051474)
BOTTOM RIGHT: (-59.20485772277679, -62.287273236674736)
Datos Originales: 
    class   x_center   y_center  width  height
0      0 -59.209791 -62.285558     30      30
1      0 -59.209815 -62.285566     30      30
2      0 -59.209862 -62.285563     30      30
3      0 -59.209878 -62.285563     30      30
4      0 -59.209861 -62.285556     30      30
Datos filtrados guardados en 'coords/coords_per_tile/coords_recorte_7.csv'.


Recortando imagen recorte_8.tif...
_________________________________________________________
Metadata:
---------
driver: GTiff
dtype: 

In [3]:
# PARTE 3: ASIGNACIÓN DE LABELS EN TXT A CADA SUBRECORTE

yolo_fun.generar_txt_yolo(
    subrecorte_dir = subrecortes_dir, 
    csv_file = orthomosiac_coords, 
    coords_dir = coords_dir_sin_normalizar
)

Generando archivos .txt: 100%|██████████| 278/278 [00:04<00:00, 61.87it/s]

Archivos .txt generados en coords\labels_sin_normalizar


In [4]:


# Iteramos para normalizar las coordenadas de cara archivo.txt
for file in os.listdir(coords_dir_sin_normalizar):
    df_sin_normalizar = pd.read_csv(os.path.join(coords_dir_sin_normalizar, file), sep=' ', header=None)
    name_subrecorte = os.path.splitext(file)[0]
    subrecorte_file = os.path.join('cut_tiles', f"{name_subrecorte}.tiff")

    print(f"Normalizando archivo {file}...")
    coords_file = os.path.join(coords_dir_sin_normalizar, file)
    output_file = os.path.join(coords_dir_normalized, file)
    
    yolo_fun.normalize_yolo_coords(
        tiff_file = subrecorte_file,
        coords_sin_normalizar = df_sin_normalizar, 
        output_file = output_file, 
    )


Normalizando archivo recorte_12_-59.233024253084785_-62.28985315757073.txt...
Normalizando archivo recorte_12_-59.233024253084785_-62.289945297602735.txt...
Normalizando archivo recorte_12_-59.23322219510079_-62.28976101753874.txt...
Normalizando archivo recorte_12_-59.23322219510079_-62.28985315757073.txt...
Normalizando archivo recorte_12_-59.23322219510079_-62.289945297602735.txt...
Normalizando archivo recorte_12_-59.23342013711679_-62.28985315757073.txt...
Normalizando archivo recorte_12_-59.23342013711679_-62.289945297602735.txt...
Normalizando archivo recorte_14_-59.22073226008078_-62.288102496962736.txt...


c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:109: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0     0.046875
1     0.046875
2     0.046875
3     0.046875
4     0.046875
5     0.046875
6     0.046875
7     0.046875
8     0.046875
9     0.046875
10    0.046875
11    0.046875
12    0.046875
13    0.046875
14    0.046875
15    0.046875
16    0.046875
17    0.046875
18    0.046875
19    0.046875
20    0.046875
21    0.046875
22    0.046875
23    0.046875
24    0.046875
Name: 3, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 3] = coords_sin_normalizar.iloc[:, 3] / width  # Normalización del ancho
c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:110: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future erro

Normalizando archivo recorte_14_-59.22073226008078_-62.28819463699474.txt...
Normalizando archivo recorte_14_-59.22093020209678_-62.288010356930734.txt...
Normalizando archivo recorte_14_-59.22093020209678_-62.288102496962736.txt...
Normalizando archivo recorte_14_-59.22093020209678_-62.28819463699474.txt...
Normalizando archivo recorte_14_-59.22112814411278_-62.288010356930734.txt...
Normalizando archivo recorte_14_-59.22112814411278_-62.288102496962736.txt...
Normalizando archivo recorte_14_-59.22112814411278_-62.28819463699474.txt...
Normalizando archivo recorte_14_-59.22112814411278_-62.28874747718674.txt...


c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:109: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0    0.05042
Name: 3, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 3] = coords_sin_normalizar.iloc[:, 3] / width  # Normalización del ancho
c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:110: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0    0.046875
Name: 4, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 4] = coords_sin_normalizar.iloc[:, 4] / height  # Normalización de la altura
c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:109: FutureWarni

Normalizando archivo recorte_14_-59.22112814411278_-62.288839617218734.txt...
Normalizando archivo recorte_14_-59.22112814411278_-62.28893175725074.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.28791821689874.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.288010356930734.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.288102496962736.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.28874747718674.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.288839617218734.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.28893175725074.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.28902389728274.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.289116037314734.txt...
Normalizando archivo recorte_14_-59.221326086128784_-62.28920817734674.txt...


...

c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:109: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0     0.046875
1     0.046875
2     0.046875
3     0.046875
4     0.046875
5     0.046875
6     0.046875
7     0.046875
8     0.046875
9     0.046875
10    0.046875
11    0.046875
12    0.046875
13    0.046875
14    0.046875
15    0.046875
16    0.046875
17    0.046875
18    0.046875
19    0.046875
20    0.046875
21    0.046875
22    0.046875
Name: 3, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 3] = coords_sin_normalizar.iloc[:, 3] / width  # Normalización del ancho
c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:110: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0     0.04

Normalizando archivo recorte_7_-59.21011298020679_-62.285822990962735.txt...
Normalizando archivo recorte_7_-59.21011298020679_-62.28591513099474.txt...
Normalizando archivo recorte_7_-59.21011298020679_-62.28600727102674.txt...
Normalizando archivo recorte_7_-59.21011298020679_-62.286099411058736.txt...
Normalizando archivo recorte_7_-59.21011298020679_-62.28619155109074.txt...
Normalizando archivo recorte_7_3456_0.txt...
Normalizando archivo recorte_7_3456_384.txt...
Normalizando archivo recorte_7_3840_0.txt...
Normalizando archivo recorte_7_3840_384.txt...
Normalizando archivo recorte_7_4224_0.txt...
Normalizando archivo recorte_7_4224_384.txt...
Normalizando archivo recorte_7_5376_0.txt...
Normalizando archivo recorte_7_5760_0.txt...
Normalizando archivo recorte_7_6144_0.txt...


c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:109: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0    0.046875
1    0.046875
2    0.046875
3    0.046875
4    0.046875
5    0.046875
6    0.046875
Name: 3, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 3] = coords_sin_normalizar.iloc[:, 3] / width  # Normalización del ancho
c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:110: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0    0.046875
1    0.046875
2    0.046875
3    0.046875
4    0.046875
5    0.046875
6    0.046875
Name: 4, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 4] = coords_sin

Normalizando archivo recorte_7_6144_384.txt...
Normalizando archivo recorte_7_6528_0.txt...
Normalizando archivo recorte_7_6528_384.txt...
Normalizando archivo recorte_7_6912_0.txt...


c:\Users\Administrador.CRISASUSESTUDIO\Desktop\projects\CountingPenguins\utils\yolo_fun.py:110: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0     0.046875
1     0.046875
2     0.046875
3     0.046875
4     0.046875
5     0.046875
6     0.046875
7     0.046875
8     0.046875
9     0.046875
10    0.046875
11    0.046875
12    0.046875
13    0.046875
14    0.046875
15    0.046875
16    0.046875
17    0.046875
18    0.046875
19    0.046875
20    0.046875
21    0.046875
22    0.046875
23    0.046875
24    0.046875
25    0.046875
26    0.046875
27    0.046875
28    0.046875
29    0.046875
30    0.046875
31    0.046875
32    0.046875
33    0.046875
34    0.046875
35    0.046875
36    0.046875
37    0.046875
Name: 4, dtype: float64' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  coords_sin_normalizar.iloc[:, 4] = coords_sin_normalizar.iloc[:, 4] / height  # Normalización de la al

In [2]:


# PARTE 4: CLASIFICAR CONJUNTOS DE TRAIN Y VAL
for n_tile in range(14, 99):
    try:
        counter = 0
        subrecorte_dir = os.path.join('cut_tiles')
        for img in os.listdir(subrecorte_dir):
          
            img_name = os.path.splitext(img)[0]  # Divide entre el nombre del archivo y la extensión
            txt_path = os.path.join(coords_dir_normalized, f'{img_name}.txt')
            
            if os.path.getsize(txt_path) > 0:  # Solo copiar si el archivo .txt tiene contenido
                img_full_path = os.path.join(subrecorte_dir, img)
                txt_full_path = os.path.join(coords_dir_normalized, f'{img_name}.txt')

                # Alternar entre train y val con el contador
                if counter >= 9:
                    shutil.copy(img_full_path, os.path.join('datasets', 'penguin_dataset', 'images', 'val'))
                    shutil.copy(txt_full_path, os.path.join('datasets', 'penguin_dataset', 'labels', 'val'))
                    print(f"Imagen {img} y archivo {txt_path} copiados a 'datasets/penguin_dataset/images/val' y 'datasets/penguin_dataset/labels/val'.")
                else:
                    shutil.copy(img_full_path, os.path.join('datasets', 'penguin_dataset', 'images', 'train'))
                    shutil.copy(txt_full_path, os.path.join('datasets', 'penguin_dataset', 'labels', 'train'))
                    print(f"Imagen {img} y archivo {txt_path} copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.")
                
                counter = 0 if counter >= 10 else counter + 1
            
            else:
                print(f"Archivo {txt_path} vacío. No se copiará la imagen {img}.")
  
    except FileNotFoundError as e:
        print(f"Error: {e}")
        continue
    except Exception as e:
        print(f"Error: {e}")
        continue

Imagen tile_13_subrecorte_316.tiff y archivo coords\labels_normalized\tile_13_subrecorte_316.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_317.tiff y archivo coords\labels_normalized\tile_13_subrecorte_317.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_368.tiff y archivo coords\labels_normalized\tile_13_subrecorte_368.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_371.tiff y archivo coords\labels_normalized\tile_13_subrecorte_371.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_372.tiff y archivo coords\labels_normalized\tile_13_subrecorte_372.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_379.tiff y archivo 